TLDR:

Uses new libraries for improved content scraping:
- pypdf2 for those urls that are actually pdf
- wikipediaapi for those that are wikipedia
- requests, readability-lxml and html2text for most others
- requests, beautifulsoup and html2text for bbc

In [1]:
import json
import pickle
import PyPDF2
import html2text
import random
import requests
import wikipediaapi
import pandas as pd
from io import BytesIO
from tqdm import tqdm
import idna
from bs4 import BeautifulSoup, Comment
from concurrent.futures import ThreadPoolExecutor, as_completed
from typing import Optional, List, Dict, Tuple, Union, Any, Callable
from urllib.parse import urlparse, quote
import socket
import concurrent
from readability import Document
# from newspaper import Article

from IPython.display import display, HTML, Markdown

pd.set_option('display.precision', 5)

/var/folders/l_/g22b1g_n0gn4tmx9lkxqv5x00000gn/T/ipykernel_25290/4165680045.py:8: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [2]:
# load all questions
path = "../benchmark/data/autocast/autocast_questions.json"
df = pd.read_json(path)
print(df.shape)

# filter out non-true/false questions
df = df[df["qtype"] == "t/f"].reset_index(drop=True)
print(df.shape)

# make sure answers is not None
df = df[df["answer"].notnull()].reset_index(drop=True)
print(df.shape)

# make sure source_links is not []
df = df[df["source_links"].map(len) > 0].reset_index(drop=True)
print(df.shape)

(6532, 14)
(3225, 14)
(2003, 14)
(1403, 14)


In [3]:
# number of links per question
df['num_links'] = df['source_links'].apply(lambda x: len(x))

In [4]:
all_questions = [q for questions in df["source_links"] for q in questions if q not in ["", None]]
all_questions = list(set(all_questions))
len(all_questions)

47357

In [5]:
# remove questions that ends in image extensions (png, jpg, jpeg, gif, svg)
image_extensions = ["png", "jpg", "jpeg", "gif", "svg"]
all_questions = [q for q in all_questions if not q.endswith(tuple(image_extensions))]
len(all_questions)

47130

### Extractions

In [6]:
HTTP_TIMEOUT = 60

def get_hostname(url: str) -> str:
    """Extracts and validates the hostname from a URL."""
    if not url:
        return False

    try:
        parsed_url = urlparse(url)
        if not parsed_url.scheme:
            return False

        hostname = parsed_url.hostname
        if not hostname:
            return False

        # Check for consecutive periods in the hostname
        if '..' in hostname:
            return False

        # IDNA encoding for internationalized domain names
        hostname = idna.encode(hostname).decode('ascii')

        if len(hostname) > 255:
            return False

        return True

    except Exception as e:
        return False
    

def extract_bbc_text(url: str, num_words: Optional[int] = None) -> str:
    """Extract text from a single HTML document using html2text, removing scripts, nav, header, and footer."""
    try:
        response = requests.get(url, timeout=HTTP_TIMEOUT)
        response.raise_for_status()
        html = response.text
        soup = BeautifulSoup(html, "html.parser")

        # Remove unwanted elements
        for element in soup([
            "script", "style", "nav", 
            "header", "footer", "form", 
            "iframe", ".navbar", ".menu", 
            ".breadcrumb", ".pagination", ".nav",
            ".ad", ".sidebar", ".popup", ".modal",
            ".social-icons", ".hamburger-menu",
        ]):
            element.decompose()

        # Remove comments
        for comment in soup.find_all(text=lambda text: isinstance(text, Comment)):
            comment.extract()

        # Convert to text using html2text
        h = html2text.HTML2Text()
        h.ignore_links = True
        h.ignore_images = True
        h.ignore_emphasis = True
        text = h.handle(str(soup))

        # Trim to a specific number of words if required
        if num_words:
            words = text.split()[:num_words]
            words = ' '.join(words)

            return {"url": url, "error": False, "error_message": None, "text": words}

        return {"url": url, "error": False, "error_message": None, "text": text}
    
    except Exception as e:
        print(f"Error extracting text from {url}: {e}")
        return {"url": url, "error": True, "error_message": str(e), "text": None}


def extract_default_text(url: str, num_words: Optional[int] = None) -> str:
    """Extract text from a single HTML document using html2text."""
    try:
        response = requests.get(url, timeout=HTTP_TIMEOUT)
        response.raise_for_status()
        doc = Document(response.text)
        readable_article = doc.summary()
        
        # use html2text to convert HTML to markdown
        h = html2text.HTML2Text()
        h.ignore_links = True
        h.ignore_images = True
        h.ignore_emphasis = True
        text = h.handle(readable_article)

        # Trim to a specific number of words if required
        if num_words:
            words = text.split()[:num_words]
            return ' '.join(words)
        
        return {"url": url, "error": False, "error_message": None, "text": text}

    except Exception as e:
        print(f"Error extracting text from {url}: {e}")
        return {"url": url, "error": True, "error_message": str(e), "text": None}


def extract_from_wikipedia(url: str, num_words: Optional[int] = None) -> Dict[str, Any]:
    """Extract full text from a Wikipedia page using the wikipedia-api wrapper."""

    wiki = wikipediaapi.Wikipedia(user_agent='MyWikiExtractor/1.0 (example@gmail.com)')

    try:
        # Extract the page title from the URL
        title = url.split("/")[-1]

        page = wiki.page(title)
        if page.exists():
            # Use 'text' property to get full content of the page
            text = page.text

            # Optionally, trim the text
            if num_words:
                words = text.split()[:num_words]
                text = ' '.join(words)

            return {"url": url, "error": False, "error_message": None, "text": text}
        else:
            return {"url": url, "error": True, "error_message": "Wikipedia page does not exist", "text": None}
    except Exception as e:
        return {"url": url, "error": True, "error_message": str(e), "text": None}


def extract_text_from_pdf(url: str, num_words: Optional[int] = None) -> Dict[str, Any]:
    """Extract text from a PDF document at the given URL."""
    try:
        response = requests.get(url, timeout=HTTP_TIMEOUT)
        response.raise_for_status()
        
        if 'application/pdf' not in response.headers.get('Content-Type', ''):
            return ValueError("URL does not point to a PDF document")
        
        with BytesIO(response.content) as pdf_file:
            reader = PyPDF2.PdfReader(pdf_file)
            text = ""
            for page in reader.pages:
                text += page.extract_text()
            # Optionally, trim the text to the specified number of words
            if num_words:
                words = text.split()[:num_words]
                text = ' '.join(words)

            return {"url": url, "error": False, "error_message": None, "text": text}
    
    except Exception as e:
        print(f"Error extracting text from {url}: {e}")
        return {"url": url, "error": True, "error_message": str(e), "text": None}


def get_text(url: str, num_words: Optional[int] = None) -> Dict[str, Any]:
    """Get the content of a URL and extract text. Handles both HTML and PDF."""
    hostname = get_hostname(url)
    if not hostname:
        return {"url": url, "error": True, "error_message": "Invalid hostname", "text": None}

    filter_words = [
        "facebook", "twitter", "youtube",
        "instagram", "pinterest", "linkedin", "bloomberg",
    ]
    if any(word in url.lower() for word in filter_words):
        print(f"URL filtered: {url}")
        return {"url": url, "error": True, "error_message": "URL filtered", "text": None}
    
    # Extract text from pdf
    if url.lower().endswith(".pdf"):
        return extract_text_from_pdf(url, num_words)
    
    # Extract text from wikipedia
    if "wikipedia" in url.lower():
        return extract_from_wikipedia(url, num_words)
    
    # if bbc in url, use custom function to extract text
    if "bbc" in url.lower():
        return extract_bbc_text(url, num_words)
    
    # Extract text from other websites
    return extract_default_text(url, num_words)

In [7]:
def process_urls_chunk(urls_chunk):
    """Process a chunk of URLs and return their processed data."""
    processed_data = []
    for url in tqdm(urls_chunk, desc="Processing URLs", total=len(urls_chunk)):
        processed_result = get_text(url)
        processed_data.append(processed_result)
    return processed_data

def save_progress(data, filename):
    """Save the processed data to a file."""
    with open(filename, 'ab') as file:
        pickle.dump(data, file)

def process_urls_concurrently(urls, chunk_size=1000, max_workers=10):
    for i in range(0, len(urls), chunk_size):
        urls_chunk = urls[i:i + chunk_size]
        with concurrent.futures.ThreadPoolExecutor(max_workers=max_workers) as executor:
            future = executor.submit(process_urls_chunk, urls_chunk)
            processed_data = future.result()
            save_progress(processed_data, f'processed_urls_{i // chunk_size}.pickle')


In [60]:
process_urls_concurrently(all_questions, chunk_size=1000, max_workers=10)

Processing URLs:   0%|          | 3/1000 [00:00<04:38,  3.58it/s]

Error extracting text from http://researchbriefings.files.parliament.uk/documents/CBP-7886/CBP-7886.pdf: 403 Client Error: Forbidden for url: http://researchbriefings.files.parliament.uk/documents/CBP-7886/CBP-7886.pdf


Processing URLs:   0%|          | 4/1000 [00:01<07:55,  2.09it/s]

Error extracting text from http://www.chicagotribune.com/news/sns-wp-blm-islamicstate-comment-2bb6f8fc-b306-11e5-8abc-d09392edc612-20160104-story.html: 404 Client Error: Not Found for url: https://www.chicagotribune.com/news/sns-wp-blm-islamicstate-comment-2bb6f8fc-b306-11e5-8abc-d09392edc612-20160104-story.html


Processing URLs:   0%|          | 5/1000 [00:03<14:59,  1.11it/s]/var/folders/l_/g22b1g_n0gn4tmx9lkxqv5x00000gn/T/ipykernel_72301/2880459533.py:53: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  for comment in soup.find_all(text=lambda text: isinstance(text, Comment)):
Processing URLs:   1%|          | 8/1000 [00:06<16:49,  1.02s/it]

...

Processing URLs:  97%|█████████▋| 126/130 [11:14<00:06,  1.69s/it]

Error extracting text from http://inhomelandsecurity.com/zika-virus-map-shows-america-next/?utm_source=IHS: 403 Client Error: Forbidden for url: https://amuedge.com/zika-virus-map-shows-america-next/?utm_source=IHS


Processing URLs:  98%|█████████▊| 128/130 [11:28<00:07,  3.92s/it]

Error extracting text from http://globalriskinsights.com/2016/04/south-korea-parliamentary-elections/: 403 Client Error: Forbidden for url: http://globalriskinsights.com/2016/04/south-korea-parliamentary-elections/


Processing URLs: 100%|██████████| 130/130 [11:32<00:00,  5.32s/it]


In [42]:
# load all processed data
processed_data = []
for i in range(0, len(all_questions), 1000):
    with open(f'processed_urls_{i // 1000}.pickle', 'rb') as file:
        processed_data.extend(pickle.load(file))

In [43]:
# save it as a pickle file
with open("retrieved_docs_v3.pickle", "wb") as file:
    pickle.dump(processed_data, file)

In [44]:
# remove non dictionary items
processed_data = [d for d in processed_data if isinstance(d, dict)]

In [45]:
docs_df = pd.DataFrame(processed_data)
print(docs_df.shape)

# remove duplicates
docs_df = docs_df.drop_duplicates(subset=["url"]).reset_index(drop=True)
print(docs_df.shape)

(46083, 4)
(46073, 4)


In [46]:
docs_df_error = docs_df[docs_df["error"] == True].reset_index(drop=True)
docs_df_error.shape

(18255, 4)

In [47]:
docs_df_no_error = docs_df[docs_df["error"] == False].reset_index(drop=True)
docs_df_no_error.shape

(27818, 4)

In [48]:
def count_no_error_links(row):
    count = 0
    for link in row["source_links"]:
        if link in docs_df_no_error["url"].values:
            count += 1

    return count

df["num_no_error_links"] = df.apply(count_no_error_links, axis=1)

In [49]:
# number of questions with no error links minimum 5 no error links
min_no_error_links = 5
df["num_no_error_links"].value_counts().sort_index()[min_no_error_links:].sum()

602

In [50]:
docs_df_no_error['num_words'] = docs_df_no_error['text'].apply(lambda x: len(x.split()))

In [51]:
docs_df_no_error['num_words'].quantile([0.25, 0.50, .75, .9, .95, .99])

0.25      140.00
0.50      511.00
0.75     1013.00
0.90     1915.00
0.95     3860.00
0.99    13079.94
Name: num_words, dtype: float64

In [52]:
# count number of source links that are more than n words
n_words = 1000
def count_num_words(row, n):
    count = 0
    for link in row["source_links"]:
        if link in docs_df_no_error["url"].values:
            num_words = docs_df_no_error[docs_df_no_error["url"] == link]["num_words"].values[0]
            if num_words > n:
                count += 1

    return count

df["num_words_1000"] = df.apply(lambda x: count_num_words(x, n_words), axis=1)

In [53]:
df["num_words_1000"].value_counts().sort_index()[min_no_error_links:].sum()

340

### Making final dataset

we filter out the following
- non 200 codes
- urls with certain keywords that were identified during manual checking
- use of html2text
- use pdf extractor for pdfs
- use wikipedia api for wikis
- and finally, filter links that had less than 1000 words
- the final dataset will have a minimum of 5 and maximum of 20 source_links 

In [54]:
final_df = df.copy()

In [55]:
# keep only questions with at least 5 links and more than 1000 words
final_df = final_df[final_df["num_words_1000"] >= min_no_error_links].reset_index(drop=True)

In [56]:
# source_links remove links that are not in docs_df_no_error and keep only links that have more than 1000 words
def filter_source_links(row):
    links = []
    for link in row["source_links"]:
        if link in docs_df_no_error["url"].values:
            num_words = docs_df_no_error[docs_df_no_error["url"] == link]["num_words"].values[0]
            if num_words > n_words:
                links.append(link)

    return links

final_df["source_links"] = final_df.apply(filter_source_links, axis=1)

In [57]:
# verify that all links are in docs_df_no_error and have more than 1000 words
for links in final_df["source_links"]:
    for link in links:
        assert link in docs_df_no_error["url"].values
        assert docs_df_no_error[docs_df_no_error["url"] == link]["num_words"].values[0] > n_words

In [58]:
# from final_df remove added columns
final_df = final_df.drop(columns=["num_links", "num_no_error_links", "num_words_1000"])

# convert to json
final_df.to_json("autocast_questions_filtered_v3.json", orient="records")

In [59]:
# from docs_df_no_error keep only urls that are in final_df
docs_df_no_error = docs_df_no_error[docs_df_no_error["url"].isin(final_df["source_links"].explode().unique())].reset_index(drop=True)

# drop error, error_message, num_words
docs_df_no_error = docs_df_no_error.drop(columns=["error", "error_message", "num_words"])

In [60]:
# save as pickle
with open("autocast_questions_filtered_v3.pkl", "wb") as f:
    pickle.dump(docs_df_no_error, f)

### Verify saved files

In [61]:
import json

with open("autocast_questions_filtered_v3.json", "r") as f:
    data = json.load(f)

In [66]:
len(data), data[0]

(340,
 {'question': 'Will the Export-Import Bank of the United States be re-authorized before 1 January 2016?',
  'id': 'G5',
  'background': "The Export-Import Bank's authorization expired on 1 July, but proponents of the bank are working to get it re-authorized (http://www.nytimes.com/2015/07/01/business/international/though-charter-is-expiring-export-import-bank-will-keep-its-doors-open.html , http://www.nytimes.com/2015/07/06/us/politics/us-export-import-bank-teetering-on-edge.html , http://thehill.com/policy/finance/247953-house-gop-draws-first-in-ex-im-showdown ). Legislation re-authorizing the bank must be signed into law by the President before taking effect.",
  'publish_time': 1441116141242,
  'close_time': '2015-12-04 14:00:25+00:00',
  'tags': ['Economic Policy', 'US Politics', 'US Policy'],
  'source_links': ['http://www.hartfordbusiness.com/article/20151005/NEWS01/310029963',
   'http://breakingdefense.com/2015/09/theyre-back-congress-likely-to-pass-short-term-budget-deal

In [63]:
with open("autocast_questions_filtered_v3.pkl", "rb") as f:
    docs = pickle.load(f)

In [64]:
docs

url  \
0     https://www.chinafile.com/viewpoint/future-of-...   
1     http://www.businessinsider.com/donald-trump-jr...   
2     http://www.pewresearch.org/fact-tank/2016/05/0...   
3     https://en.wikipedia.org/wiki/U.S._sanctions_a...   
4     http://www.cbc.ca/news/politics/premiers-court...   
...                                                 ...   
6100  https://www.theguardian.com/commentisfree/2017...   
6101  https://en.wikipedia.org/wiki/Geryon#The_Tenth...   
6102      http://www.bbc.com/news/world-europe-35118927   
6103  https://www.bbc.com/news/world-middle-east-560...   
6104  https://www.washingtonpost.com/world/saudi-ara...   

                                                   text  
0     In early August, Beijing held show trials of f...  
1     This March 16, 2016 file photo shows Trump Tow...  
2     For decades the gold standard for public opini...  
3     The United States has since 1979 applied vario...  
4     A potential showdown is looming over the feder...  
...                                                 ...  
6100  Home from chasing lost sheep on a beautiful su...  
6101  In Greek mythology, Geryon ( or ; also Geryone...  
6102  This video can not be played\n\n## To play thi...  
6103  Image source, Reuters\n\nImage caption,\n\nThe...  
6104  BEIRUT — Saudi Arabia severed diplomatic relat...  

[6105 rows x 2 columns]

In [83]:
display(Markdown(docs.loc[876, "text"]))

Why is Britain eurosceptic? 
By Charles Grant
The British have never been terribly popular members of the European Union. Long before they joined,
many continentals thought them too different to be constructive members of what was then the European
Economic Community (EEC). In January 1963 General de Gaulle held a press conference to set out hisreasons for vetoing Harold Macmillan’s application for membership. Some, though not all of his arguments,
still resonate today.
Britain is insular, maritime, bound up by its trade, its markets, its food supplies, with the most varied and
often the most distant countries. Her activity is essentially industrial and commercial, not agricultural.She has, in all her work, very special, very original, habits and traditions. In short, the nature, structure,
circumstances peculiar to England are very different from those of other continentals. How can Britain,in the way that she lives, pr oduces, trades, be incorporated into the Common Market as it has been
conceived and functions?… It is predictable that the cohesion of all its members, which would soon bevery large, very diverse, would not last for very long and that, in fact, it would seem like a colossalAtlantic community under American dependence and dir ection, and that is not at all what France wanted
to do and is doing, which is a strictly Eur opean constr uction.
Exactly ten years later Britain joined the EEC. But the British have never been at ease in what has become
the EU. They ar e mor e hostile to the EU than any other Eur opean people. British gover nments, too, have
often used their influence to slow down Eur opean integration. Thus Britain has opted out of the euro and
the Schengen agr eement, and pr evented the extension of qualified majority voting into ar eas such as tax,
foreign policy and defence. Ther e is no r eason to think that this attitude will change. Gordon Brown’s
government is less enthusiastic about the EU than that of his predecessor, Tony Blair. And if the
Conservative Party wins the next general election, as seems plausible at the time of writing, a governmentled by David Cameron will be markedly more eurosceptic than that led by Brown.
Some of the British people’s disdain towards the EU and things European is reciprocated. Many Britons
would be surprised to know just how fed up many other Europeans are with their attitude to the EU. Yearsof British leaders preaching – sometimes arrogantly – about the success of their economic model, a foreignpolicy that often appears subservient to that of the US, a penny-pinching approach to the EU budget and aconsistently negative attitude to treaty change have left their mark. The kinds of argument that de Gaullemade in the 1960s can still be heard.
People on the continent tend to overlook the positive impact of Britain on the EU. I would argue that Britain
is far from being the most eurosceptic member-state, defined as the one that causes the most damage to theEU. The British have a good r ecord of implementing EU directives and of respecting the decisions of the
European Court of Justice, while a supposedly pro-EU country such as France has a poor record on those
counts. At the level of EU policy-making, British influence has been considerable and often positive. The‘1992 pr ogramme’ that led to the single market was drawn up by a British Conservative commissioner, Lord
Cockfield. Tony Blair, together with the then French president Jacques Chirac, wrote the Saint Malo
declaration of 1998, which led to the EU developing military capabilities. The ‘Lisbon agenda’ of economicreform, established in 2000, had considerable British input. Britain has championed the enlargement of the
Union and the concept of economic openness (though not everyone shares my view that those objectives aredesirable). It has made a big contribution to the EU’s regulatory agenda, for example through the idea of‘unbundling’ (the separation of retail networks from the supply of a public service such as energy). 
essaysessays
Centre for European Reform T: 00 44 20 7233 1199
14 Great College Street F: 00 44 20 7233 1117London SW1P 3RX UK info@cer .org.uk / www .cer.org.uk2
Britain takes the ‘four freedoms’ (the free movement of capital, goods, labour and services) more seriously
than many countries that r egard themselves as fully committed to the EU. Thus Britain has encouraged
French and German companies to buy up most of its utilities, though the favour has not been returned; it
is the only large EU country that has allowed other European firms to purchase big chunks of its defenceindustr y; and when eight Central and East European countries joined the EU in 2004, initially only Britain,
Ireland and Sweden opened their labour markets to workers from the new members. 
On balance I would argue that British influence on the EU has been more beneficial than harmful.
Nevertheless I have no doubt that the euroscepticism of the British is a serious problem, not only for any
UK government that tries to engage with the EU, but also for other Europeangovernments. British ministers often oppose measures coming out of Brussels orother capitals because they fear the reaction of the British media or public. 
This essay analyses the reasons for British people disliking the EU, looking at
geography, history, economics and, especially, the media. It asks why Britain’s
ruling classes have been unwilling to try and shift opinion in a more EU-friendlydirection. And it concludes with the prediction that, in the very long run, Britain
will take a more positive line on the EU.
1
Geography, history and economics
The regular Eurobarometer surveys of public opinion, carried out by the European Commission, suggest
that the British are the most eurosceptic people in Europe. A Eurobarometer survey published by theCommission in June 2008 asked whether membership of the EU was a good thing. The average response
of citizens across the EU was that 52 per cent thought it a good thing.
2But in the UK the answer was 30
per cent, with only Latvia on 29 per cent scoring lower . Then Eurobarometer
asked respondents if their country benefited from membership. The average
positive response was 54 per cent, but only 36 per cent of Britons (and Austrians and Hungarians) thought
their countr y had benefited. 
Eurobarometer also asked whether people trusted EU institutions. For the Commission, the average answer
across the EU was 47 per cent. In the UK it was 24 per cent, a much lower per centage than in the next most
Commission-phobic countr y, Latvia, wher e it was 37 per cent. As for the Eur opean Parliament, 52 per cent
of EU citizens tr ust it, but only 27 per cent of Britons. The British results in this Eurobarometer survey were
a little mor e positive than in the pr evious poll, published in December 2007, per haps because in the second
half of 2007 ar guments about tr eaty change and r eferendums fuelled eurosceptic sentiment in the UK.
When I travel around Europe, and people ask me why the British are eurosceptic, I offer four explanations
– three of which are easily understood. The first of these is geography and the effect it has had on Britishhistory. The British people live on an island on the edge of the continent and have always been inspired bythe oceans. The British talk of Europe as another place (as the Finns, Irish and Portuguese sometimes do).Britain’s history has been very different to that of most continental powers. Its colonies, trade, investmentsand patterns of emigration and immigration have been focused on North and South America, Africa andAsia as much as on Europe. To some extent France, Holland, Spain and Portugal shared this maritimeexperience, while the other European states sought to build empires or wield influence mainly in theirneighbourhoods. Although Britain has been involved in countless European wars, its history has been moreorientated to other continents than that of any continental power. Even France, which had colonies all overthe world, has focused its ambitions on Europe for much of its history. 
Today, London is by far the most cosmopolitan city in Europe; more than 30 per cent of its population was
born outside the UK. Although a little more than half of Britain’s merchandise trade is now with the rest of
the EU, many Britons believe that their country would flourish as a global hub for trade and investment,outside the EU, unencumber ed by the rules and regulations of Brussels. Churchill famously told de Gaulle
that, faced with a choice between the continent and 
le grand large , the British would always choose the wide
open seas.
Britain’s relatively glorious role in the Second World War plays a potent role in nourishing euroscepticism.
Virtually every other major European nation has something to be ashamed of in that war. A lot of countrieswere on the wrong side. Others were conquered. And others stayed neutral. British popular culture is stillheavily focused on the Second World War as the country’s ‘finest hour’. Other countries have moved on,and suppor ted the EU as means of ensuring that the hor rors of the Nazi period can never be r epeated. But
the British do not want to for get the histor y of which they feel pr oud. Memories of the war give them a2 Eurobarometer 69, June 2008.1 An earlier version of this essay
appeared in French in ‘Notre
Europe’, a book edited by Michel
Rocard and Nicole Gnesotto and
published by Robert Laffont in
2008. This revised version has 
benefited fr om the comments of
Katinka Barysch, Hugo Brady,Clara Marina O’Donnell, 
Simon Tilford and Philip Whyte. smug sense of moral superiority vis-à-vis most of the other peoples of Europe. Margaret Thatcher often said
that the continent of Eur ope has been the source of most of Britain’s ills, and that the Anglo-Saxon nations,
and in particular the Americans, have repeatedly rescued Britain from those ills. Many Britons, especially
the older generation, would agree with her.
In addition to geography and history, economics helps to explain British euroscepticism. Since the mid-
1990s, the UK economy has out-performed the leading economies of Western Europe – France,Germany and Italy – by most measures. Britain has had relatively high growth and low unemployment.Its economy has some evident weaknesses, such as quite poor productivity. But Britain has appeared to
benefit from the structural reforms of the Thatcher period, such as the liberalisation of labour markets,the openness to foreign investment and – though this is now open to some challenge – the fostering ofvibrant financial markets. 
In the 1970s, Britain was regularly described as the sick man of Europe; nowadays that epithet is most often
applied to Italy. In the late 1990s and early 2000s the unemployment rate in Spain, Italy, France and
Germany was around twice that of the UK. The contrast in economic fortunes between Britain and theeurozone is the biggest reason why Tony Blair’s government never found the courage to fight a referendum
on joining the euro. So long as Euroland seemed beset with economic problems, and Britain was booming,it was extremely hard to make a convincing case that joining the euro would benefit the UK. In the 1980s,
many British politicians had argued that Britain had a lot to learn from the way that France and Germany
ran their economies. By the late 1990s the predominant view in the UK was that the rest of Europe had alot to learn from the British.
Of course, the financial crash of 2008, and the fact that Britain is entering a particularly severe recession,
is likely to diminish the hubris of Britain’s political class about their economic model. It is no longer self-evident that an economy benefits fr om being as orientated to services and financial markets as is Britain. 
However, even if the British economy performs less well than its continental peers for a few years – which
is likely – I doubt that many Britons will year n to adopt the eur o or demand that their economy be r un like
those on the continent. And despite the r ecent financial and economic tur moil, political leaders in countries
such as France, Ger many and Italy know that their economies suffer from serious structural problems and
that they need to copy many of the r eforms that the British (and the Nor dic countries) have implemented
in recent decades. 
However , if the British economy underper formed, compar ed with its peers, for a pr olonged period, one
cause of British eur oscepticism would be r emoved.
Britain’s unique media
The fourth explanation for Britain’s hostility to the EU, which is not easily understood outside the UK, is
that Britain has a uniquely powerful and eurosceptic popular press. Ironically, some of the best mediaorganisations that cover the EU, such as the 
Financial Times , The Economist and Reuters, are UK-based.
But of the roughly 30 million people who read a daily newspaper in Britain, three-quarters read papers thatare determined to make people dislike the EU. The remaining quarter read papers which, though broadlypro-European, still print much that criticises the EU. In the eurosceptic newspaper groups, journalists areexpected to write stories that knock the Union. Articles which attempt to present a balanced account of anEU issue are unlikely to be published. The 
Times and the Daily Telegraph , two serious newspapers, almost
never print an opinion piece that is supportive of the EU or what it is trying to do.
The national written pr ess is particularly influential in Britain, compared with other EU states, and the
internet has not yet changed this. The total circulation of national titles is much larger than in France: 11
million against 2.5 million (in France many more people buy regional papers and news magazines). Theownership of the UK written pr ess is also very concentrated. Four newspaper groups – the 
Daily Mail and
those controlled by Rupert Murdoch (the Sunand the Times ), Richard Desmond (the Express and the Star)
and the Barclay brothers (the Daily Telegraph ) – account for about 75 per cent of daily newspapers sold,
and generally impose a rigidly eur osceptic line on their journalists. The competition among national titles
is also very strong. This encourages bold, striking and often inaccurate front pages.
To be fair to the British tabloids, the EU sometimes does its best to help them portray the Union in a sinister
light. The annual refusal of the Court of Auditors to give an unqualified approval of the EU accountspresented the anti-EU pr ess with a field day (though in November 2008 the Cour t gave the accounts an
unqualified appr oval). So does the fact that the Common Agricultural Policy still accounts for nearly half3the EU budget, still causes great damage to farming in developing countries, and is still spent mainly on rich
farmers rather than poor ones. The inability of the EU institutions to explain simply and clearly why they
do what they do, and how EU policies and programmes help ordinary citizens, is legendary.
Never theless, in no other European country is it acceptable for leading journalists to report tendentiously
on, or even lie about, the EU. I have twice, in 2004 (at the time of the agreement on the constitutional treaty)
and in 2007 (at the time of the agreement on the Lisbon treaty), spent a couple of weeks analysingnewspaper coverage of the EU. I shall start with some examples from 2004. Edward Heathcoat-Amorywrote in the 
Daily Mail that the constitutional treaty meant the British would “have to give up our vital
seat on the UN Security Council if the EU Foreign Minister asked for it”. In the same paper Melanie Phillipssaid of the European Court of Justice that its “overt purpose is to bring about a super-state”. And in the
Times , Irwin Stelzer claimed the constitution would force Britain to give up the pound, even if there was no
UK referendum on joining the euro. 
Now for some examples from 2007. A Daily Telegraph leader said it was “an atrocity” that the royal
family’s coat of arms would be banned from the cover of British passports. A Sunday Express piece on the
European gendarme force, which involves five EU member-states (but not Britain), said that “Brussels has
set up a new EU police force that could patrol the streets of Britain”. A Sunarticle on the treaty’s passerelle
clause said that “further vetoes could be given up by EU leaders without the permission of our Parliament.”
Of course, all these claims are entirely false. In virtually any week of the year, there are similarly bogus stories
about the EU. In the words of David Rennie, the current Economist correspondent in Brussels: “The EU has
become the equivalent of the fat boy with glasses who is bullied each break time: it is just what happens, itis cost free.” That is true. So is this comment from Brian Cathcart, professor of journalism at Kingston
University. “HL Menken once said that no one ever went broke underestimating the taste of the Americanpublic; by the same token, no newspaper publisher will go br oke overestimating the euroscepticism of the
British public.”
Journalists get away with writing factual inaccuracies because they ar e accountable to no one but their
bosses and they face no sanction. The British system of pr ess regulation – r un by the Pr ess Complaints
Commission – is a voluntar y body that has no teeth and does virtually nothing to encourage truth-telling
or balance. Politicians ar e too scar ed to ask for a mor e rigor ous system of pr ess regulation, for they know
that anyone who did so would become a 
bête noir efor the tabloids. Jour nalists also get away with writing
lies about the EU because it does not, as a policy , sue in the courts.
Unfor tunately , some of the ludicr ous stories that appear in the British press really influence what politicians
say and do. For example, just before the June 2007 European Council, which approved what became the
Lisbon treaty, the Sunwas particularly vocal about the treaty’s new foreign policy provisions. A piece
headlined “Britain surrendering its seat at the UN” said that the new treaty would mean “a newinternational affairs minister dictating UK policy at the UN.” Gordon Brown, then in his last days asChancellor of the Exchequer, intervened in the Whitehall machinery to harden the UK line on the newforeign policy institutions. As a result, Foreign Secretary Margaret Beckett went to Brussels to announce atougher UK line, including a veto on the creation of the ‘external action service’, the new body designed tobring together diplomats from the member-states with those in the Council and the Commission who workon foreign policy. Then at the summit itself Prime Minister Tony Blair changed British policy back to whereit had been and accepted the external action service.
Such examples of the popular press shifting the EU policy of the Labour government are, thankfully, rare.
But the press does have a big influence on the way ministers present policy. They regularly brief the tabloidsthat they ar e fighting nefarious schemes dreamed up by the Commission or other countries. They do so in
the hope of seeing articles that portray them as fighting bloody but unbowed for the sake of British interests.
Often, however, such stories bear very little relationship to what the minister concerned has in fact said inthe Council of Ministers. The British media – and not just the tabloids, but also the BBC – like to por tray
Brussels as a story about epic battles, victories and defeats. The truth is that almost everything the EU does
helps to bring about compromises that benefit all or nearly all member-states. But that – often dull – truthdoes not make for thrilling jour nalism.
Strangely, the most eurosceptic newspapers – the ones which claim that Brussels bureaucrats exercise
increasing power over Britain – do not bother to have full-time correspondents in Brussels. They prefer towrite EU stories out of London, where of course they are less likely to get their facts right. Currently, of thenational dailies, only the 
Financial T imes, Guar dian and Times (whose editorial line is anti-EU, but whose
reporting is sometimes good) have staf f correspondents in Br ussels.4The broadcast media, and notably the BBC, tend to report more fairly than the tabloids. But BBC journalists
are prone to follow an agenda set by tabloid stories.  The BBC is often accused of elitism, especially by
eurosceptic lobbies. So it tends to bend over backwards to avoid the charge by making extra efforts to
accommodate populist and eurosceptic viewpoints. 
Of course, not everyone believes everything they read in the press. But the steady drip, drip, of anti-EU
propaganda over many years, having permeated deep into Britain’s political culture, has made a majorcontribution to the shift in British public opinion since the late 1980s: the country has become more eurosceptic. 
Politicians in the rest of Europe quite rightly ask why Britain’s leaders have to accept the tyranny of the
popular press. Why can they not take on the 
Daily Mail and the Sun, make speeches about error-prone
tabloid reporting, and explain all the good things the EU does? Part of the answer is that very few politicians
would see it as being in their interest to do so. I know pro-EU cabinet ministers in the Blair and Brown
governments who believe that if they spoke openly about their support for the EU, their careers would beseriously damaged. They are rather like homosexual ministers who, until the 1990s, had to keep quiet about
their sexual orientation for fear of the media reaction.
But part of the answer is more complicated. In most European countries, those who dislike the EU tend
to be the poor and the less educated, who fear for their future and travel little. The politicians who speak
for such people tend to come from the far left or far right. Those who are well-educated, travel a lot and
lead comfortable lives usually support the EU. The mainstream political parties in most member-statesare broadly ‘pro-European’. Britain, however, is different. A significant section of its ruling class is anti-
French, anti-German and, especially, anti-Brussels. Even amongst politically moderate and highlyintelligent people, one sometimes hears disparaging comments about theFrench and the Germans that, if said about other ethnic groups, would be
socially unacceptable.
3One of the defining characteristics of the moder n
Conservative Party is its hostility to the EU and its institutions.
Britain’s parochial ruling classes
Thus a fifth r eason for the euroscepticism of the British is cultural and social. The ruling classes – because
of the four r easons alr eady mentioned – hold attitudes to the EU that ar e not common in other member -
states. The r esult is that few political, media or business leaders have sought to lead and educate the British
people on how they benefit fr om the European Union. 
Consider the cabinet of the cur rent Labour gover nment. Only four or five of its 23 members could be
described as pro-European, with an interest in and some knowledge of the EU (though some others know
about particular areas of EU policy). The Conservative shadow cabinet is worse. I do not believe that anyof its members has devoted much time or attention to learning about the EU. The Liberal Democrat partyis something of an exception. Both the current leader, Nick Clegg, and the rival he defeated to get the job,Chris Huhne, are former MEPs with a profound knowledge of the EU. The previous leader, MenziesCampbell, is also a pro-European. 
Consider the political editors of the national daily newspapers. Only one of them could be described as
knowledgeable about Europe – and his previous job was Brussels correspondent. Of the two-dozen mostinfluential political commentators who write in the British press, perhaps only three know much about the EU.
If you want to succeed in politics or the media in Britain, make sure you do not know too much about
Europe. If you know too much you risk being branded as a nerd who is out of touch with what mostBritish people think. I once asked a Labour MP who is now a senior cabinet minister if he wanted tobe appointed a UK representative to the Convention on the Future of Europe (which helped to drawup the constitutional treaty). He told me no: although a pro-European, he thought that taking part inthe Convention would be the death of his political car eer. Ignorance of or hostility to Europe is
certainly no handicap in the world of British journalism or politics. I have heard BBC current affairs
journalists confess that they cover up their true pro-European feelings for the sake of their careers: oneof the best ways to advance is to make eur osceptic comments that get you noticed; then senior editors
will praise you for being ‘in touch’.
But what about the worlds of business and finance? Surely top businessmen and bankers understand how
the UK gains from being part of the world’s largest single market? It is true that many business leaders arebroadly pr o-Eur opean. But few of them ar e prepared to speak out on the EU. Some of them campaigned
for the eur o, but became bitter when the Labour gover nment was too cowar dly to ever make a for ceful case5
3 To be fair to the British, plenty of
French and German people speakabout ‘Anglo-Saxons’ in an equally
derogatory manner. for the single currency. Now many of these business leaders say that it is up to politicians to give a lead on
Europe. In any case, in business circles, it is increasingly fashionable to argue that the EU is an out-of-date,
failing project that will not survive the era of globalisation. Small businesses have always tended to be
eurosceptic. Many of them see the EU not as an instrument for making it easier to trade and invest abroad,or to impor t cheaper workers, but rather as a source of red tape. 
The City of London, which has thrived outside the euro – though it makes lots of money from trading paper
denominated in euros – has become markedly more anti-EU in the last ten years. Many financiers have cometo regard the EU principally as the source of every regulation they dislike. In fact the British government has
usually fought off European challenges to its own ‘light touch’ approach to financial regulation.
The EU is the source of some bothersome financial and business regulations, but the British government has
often voted in favour and then implemented them in an over-detailed manner. Bankers and business people
sometimes forget that if the EU did not set common standards on, say, the use of industrial chemicals orbank capital requirements, they could not benefit from the EU’s single market.
Business people are particularly hostile to attempts to set social or labour market norms in Brussels. That
is why the Confederation of British Industry (CBI) campaigned so vehemently against the charter offundamental rights, a non-binding set of principles that was included in both the constitutional treaty and
the Lisbon treaty. That charter contains aspirations such as the right to strike and the right to join a trade
union. Because of the CBI, the Labour government insisted on amendments to the Lisbon treaty to clarifythat the charter will have no effect in Britain. But that in turn upset Britain’s trade unions. They had become
broadly pro-European in the 1990s, thanks to Margaret Thatcher’s hostility to the EU and Jacques Delors’sadvocacy of social Europe. Now many British trade unions are fairly eurosceptic, viewing the EU as an
organisation designed to promote the interests of business.
Reasons for hope
So is Britain doomed to become ever mor e eur osceptic, and per haps one day to leave the EU? Despite
everything I have written in this essay , I do not believe this to be the case. But I am not optimistic in the
short term. The Conservatives appear to be a profoundly eurosceptic party, divided between those who
dislike the EU but accept that Britain is better of f in than out, and those who want to leave. Most of the
party’s leaders ar e ignorant about the EU and many of them have r emarkably few contacts with other
European politicians. In power, the Conservatives are likely to provoke crises in the UK-EU relationship, for
example by tr ying to pull out of the social chapter of the tr eaties or EU defence policy . However , I would
predict that after a few years the har d facts of Eur opean and global power politics – namely that Britain on
its own cannot achieve many of its objectives – will make the Conservatives more responsible. 
In the long run, I am more optimistic. Indeed, I would argue that the UK is in many ways a pro-European
country, even if its people do not understand why. To use a Marxist concept, the ‘base’ of Britain’s economyand society is profoundly European, and sooner or later the ‘superstructure’ of the political and media elitewill have to reflect that reality.
On the continent, and also in Britain, many people believe that the British economy is closer to that of the
US, with its low taxation and minimal welfare state, than those of mainland Europe. Wrong. The British,like many other Europeans, like to live in a country with quite high levels of taxation and welfare spending.For example, spending by the state as a percentage of GDP was 44.6 per cent in the UK in 2007, comparedwith a eurozone average of 46.4 per cent and the US figure of 37.4 per cent. In 2007 the German state spentless than the British state: 44.3 per cent of GDP.
Britain has a higher proportion of its workers in a trade union than most EU member-states, including
France. Over the past ten years the Labour government has roughly doubled spending on health andeducation,  bringing the level in Britain to EU nor ms. Measures of inequality remain quite high in Britain,
mainly due to the consequences of a lot of children leaving school at 16, without useful skills. However,
Italy, Greece and Portugal have higher levels of poverty and inequality – and much more labour marketregulation – than Britain. What does differentiate the UK economy from many others in the EU is not
only the size of its financial sector but also its openness to foreign investment, including takeovers byforeign firms. 
The values held by British people tend to line up with those of other Europeans, rather than Americans,
though of course ther e is much variation among the dif ferent Eur opean peoples. Britain is a secular society
in which less than 20 per cent of the population worship r egularly , while in the US about half the population6attends church once a week. Ronald Inglehart has researched values across the world’s major countries,
interviewing 120,000 people in 1999-2001. Based on those interviews, he has drawn up an index of
secular/rational values against traditional ones: on Inglehart’s measure, a society that scores 2.0 is very
secular and rational, while –2.0 indicates a very traditional society. The United States scores –0.5 on thisindex. The EU states ar e spread out between 0.35 and 1.5, Sweden and Germany having the highest figures,
with the UK, Italy, Belgium, Austria and Spain scoring about 0.4.
On international relations, too, the British are broadly European in their world view. They may not love the
EU but they do believe in multilateral systems of governance, international law and a strong UN. Many
Americans differ on those points. It is true that the British, like the French and the Americans, are morelikely to countenance the use of force to solve an international problem than are many other Europeans. Butthe British people have been almost as hostile to the US-led invasion of Iraq as most continental Europeans.
Therefore there is nothing in the structure of the British economy, or the nature of British values, that should
prevent the UK from making a positive contribution to the EU. Indeed, the way the EU is evolving should
make it easier for the British to engage. The enlargements of the EU in 2004 and 2007 have changed itsnature profoundly. With the arrival of ten Central and East European countries, there never will be a
majority of member-states in favour of the kind of highly-integrated system of European government thatseemed plausible 20 years ago, nor for a Union that seeks to act as a counterweight to the US. Most of the
new members are more or less Atlanticist, opposed to a lot of centrally-set economic and social rules, and
in favour of free trade. 
One reason why the British dislike the EU is that they have seen it as dominated by France and Germany,
promoting Franco-German interests. There was sometimes some truth in that caricature, but no longer.
France and Germany cannot dominate an EU of 27 countries. Furthermore, some of the countries that usedto be most suppor tive of European integration have recently become more sceptical of it – for example,
France, Germany, Ireland and the Netherlands. So even if the British people tend to be the most
eurosceptical, as the Eurobarometer surveys show, their views on the EU are less divergent from the rest of
Europe than they used to be.
In this wider , looser, Europe, there are bound to be groups of countries that form 
avant-gar desto hasten
integration in par ticular ar eas, as many countries have done with the eur o. But the idea that the EU as a
whole could become some sor t of super -state – an idea that nourishes much of the passion in British
eurosceptism – is now laughable. Only in Belgium and Luxembourg, and to some degree in Italy and
Germany , can one find influential politicians who ar e ‘federalist’ in the sense that Helmut Kohl and Jacques
Delors wer e in the early 1990s.
The British are the last people in Europe to understand how the EU is changing. The French understand
very well, which is why more than half of them voted against the constitutional treaty in 2005. To many ofthe French, that treaty symbolised the increasingly Ango-Saxon and economically liberal nature of the EU.Ironically, British eurosceptics opposed the treaty because they saw it as a vehicle for continental socialismand federalism.
The main reason why I am optimistic about Britain’s role in Europe is that British euroscepticism has always
been largely about institutions. It thrives when the papers are full of stories about new treaties, the loss ofnational vetoes, institutional change and the erosion of sovereignty. And ever since the Amsterdam treaty,agreed in 1997, there has been almost constant discussion of these dull and complicated but – to some – scarysubjects. The British perception of the EU is that it is all about process rather than about doing useful things.
Now, however, there is a real prospect that treaty change will be off the agenda for a long period. Either the
Irish will ratify the Lisbon treaty, allowing it to enter into force across the EU, or they will not. If the Lisbon
treaty is adopted, there will be no demand for another new treaty any time soon. The difficulties of gettingany tr eaty ratified in so many member-states are too great. If the Lisbon treaty is not adopted, some
governments will huff and puff and talk about treaty change and leadership groups, but in practice the EU
will have to learn to live with the existing treaties and all their imperfections. Either way, the EU is unlikelyto spend the next decade talking about tr eaty change.
That is good news for the British debate on Europe. The issues that will shape the way the EU develops in
the coming years – the need to tackle climate change, enhance energy security, co-operate in the fight againstcrime and terrorism, manage migration, respond to the rise of China’s economic power and stand up toRussia – ar e of huge inter est to British people. Only the most crazed of eur osceptics could ar gue that Britain
can deal ef fectively with these challenges on its own. If, as I expect, the EU focuses incr easingly on substance7rather than process, the eurosceptics will be deprived of their most powerful arguments. An EU that delivers
real benefits to the British people will become more popular, despite the best efforts of some newspapers to
tarnish its image.
#
Charles Grant is director of the Centre for European Reform. 
December 20088
For fur ther infor mation, visit our website
www .cer.org.uk

In [85]:
# verify min number of words
docs["text"].apply(lambda x: len(x.split())).min()

1001

In [86]:
# verify min 5 links
final_df["source_links"].apply(len).min()

5

In [87]:
# verify that all links are in docs
final_df["source_links"].explode().isin(docs["url"]).all()

True